(ch_GEEclassification)=
# Image classification with *GEE* and `scikit-learn`

So far, we have come a long way. We have learned to work with both, vector and raster data. We have used this knowledge to e.g., extract for specific geo-locations raster-values, to use these data for parameterizing a machine-learning classifier, and to do a subsequent prediction. Now, what this small tutorial does is show you how to do these steps using a combination of functions from the packages `scikit-learn` and `geemap`. We will exemplify this on a - admittedly not great - example. Specifically, we will collect some training data from an existing land cover dataset, and predict the same land cover categories on spectra-temporal metrics (STM). Obviously, one would expect the results to be similar, but for the sake of this tutorial, we keep it this way.

We now go step by step over the process with some example code. First, we load some packages and initialize *GEE*

In [1]:
from osgeo import ogr
from tqdm.notebook import tqdm
import json
import pandas as pd

In [2]:
import ee
import geemap.foliumap as geemap
try:
    ee.Initialize()
except Exception as e:
    ee.Authenticate()
    ee.Initialize()

## Load vector data
### Open them using the `ogr` library
First, we will load two vector files, both are located on my personal drive:
1. One file does only contain one feature, with a squared geometry. This will be our region of interest (ROI), i.e., the boundaries of our classification
2. A set of points that will serve as our training locations. This is not an uncommon scenario: often you have/receive some shapefiles in the form of points, which you use for your work.

In [3]:
roiSHP = ogr.Open("D:/OneDrive - Conservation Biogeography Lab/_TEACHING/__Classes-Modules_HUB/M8_Geoprocessing-with-python/10_Classification-and-LargeArea/01_ROI_shape.shp")
roiLYR = roiSHP.GetLayer()
roiFEAT = roiLYR[0]
roiGEOM = roiFEAT.geometry()
print(roiGEOM)

POLYGON ((13.2134494446947 52.4151979479578,13.2134494446947 52.4873242002239,13.3018503384978 52.4873242002239,13.3018503384978 52.4151979479578,13.2134494446947 52.4151979479578))


In [4]:
ptsSHP = ogr.Open("D:/OneDrive - Conservation Biogeography Lab/_TEACHING/__Classes-Modules_HUB/M8_Geoprocessing-with-python/10_Classification-and-LargeArea/02_RandomPoints_1000.shp")
ptsLYR = ptsSHP.GetLayer()
ptsLYR.GetFeatureCount()

1000

### Convert items into `ee.Geometry()` and `ee.FeatureCollection()`
Next, we will convert these items into *GEE*-Objects. The ROI we convert it into an `ee.Geometry()`, the points into an `ee.FeatureCollection()`. Both items we have already learned how to do (check the [intro chapter on *GEE* of this course](ch_introGEE)

In [5]:
geomJSON = json.loads(roiGEOM.ExportToJson())
geomCOORD = geomJSON['coordinates']
geomEE = ee.Geometry.Polygon(coords=geomCOORD)
geomEE

ee.Geometry({
  "functionInvocationValue": {
    "functionName": "GeometryConstructors.Polygon",
    "arguments": {
      "coordinates": {
        "constantValue": [
          [
            [
              13.213449444694733,
              52.41519794795775
            ],
            [
              13.213449444694733,
              52.48732420022388
            ],
            [
              13.301850338497838,
              52.48732420022388
            ],
            [
              13.301850338497838,
              52.41519794795775
            ],
            [
              13.213449444694733,
              52.41519794795775
            ]
          ]
        ]
      },
      "evenOdd": {
        "constantValue": true
      }
    }
  }
})

In [6]:
# Create an empty list that we populate
featList = []
# Iterate over all features in `ptsLYR`
for feat in tqdm(ptsLYR):
    pid = feat.GetField('Id') # Get the ID value
    # Get the geometry
    g = feat.geometry()
    gjson = json.loads(g.ExportToJson())
    gcoord = gjson['coordinates']
    gEE = ee.Geometry.Point(coords=gcoord)
    # Create ee.Feature(), append to list
    eeFeat = ee.Feature(gEE, {"UniqueID": pid})
    featList.append(eeFeat)
# Convert the list into ee.FeatureCollection()
fc = ee.FeatureCollection(ee.List(featList))
fc

  0%|          | 0/1000 [00:00<?, ?it/s]

## Prepare STM
From our chapters on [image classifications ](ch_imgclassification) and [image workflows in *GEE*](ch_imagewf) we learned what STMs are and how we can use them. Here, we repeat many of these steps, while at the same time providing some smaller functions that you can incorporate in your library.

Specifically, we take all Landsat 8 and Landsat 9 imagery of the year 2023 with less than 70% cloud cover. We merge the images of these two satellites into one collection, mask and scale the data, and calculate basic STMs.

In [7]:
def ScaleMask_l89(img):
    ## Scale the bands
    refl   = img.select(['SR_B2', 'SR_B3', 'SR_B4', 'SR_B5', 'SR_B6', 'SR_B7']).multiply(0.0000275).add(-0.2)
    img_SR = ee.Image(refl).addBands(img.select(['QA_PIXEL']))
    ## mask cloud
    # Get the QA band and apply the bits
    qa = ee.Image(img_SR).select(['QA_PIXEL'])
    dilatedCloud = qa.bitwiseAnd(1 << 1)
    cirrusMask   = qa.bitwiseAnd(1 << 2)
    cloud        = qa.bitwiseAnd(1 << 3)
    cloudShadow  = qa.bitwiseAnd(1 << 4)
    snow         = qa.bitwiseAnd(1 << 5)
    water        = qa.bitwiseAnd(1 << 7)
    # Apply the bits
    clear = dilatedCloud.Or(cloud).Or(cloudShadow).eq(0)
    cfmask = (clear.eq(0).where(water.gt(0), 1)
        .where(snow.gt(0), 3)
        .where(dilatedCloud.Or(cloud).gt(0), 4)
        .where(cloudShadow.gt(0), 2)
        .rename('cfmask'))
    img_SR_cl = ee.Image(img_SR).select(['SR_B2', 'SR_B3', 'SR_B4', 'SR_B5', 'SR_B6', 'SR_B7']).mask(cfmask.lte(2))
    return img_SR_cl

In [8]:
# Get the collections, merge them
l8 = ee.ImageCollection("LANDSAT/LC08/C02/T1_L2")\
    .filterDate('2023-03-01', '2023-11-30').filter(ee.Filter.lt('CLOUD_COVER', 70)).filterBounds(geomEE)
l9 = ee.ImageCollection("LANDSAT/LC09/C02/T1_L2")\
    .filterDate('2022-03-01', '2023-11-30').filter(ee.Filter.lt('CLOUD_COVER', 70)).filterBounds(geomEE)
lAll = l8.merge(l9)
# Apply masking and filtering
lALL_masked = lAll.map(ScaleMask_l89)
# Define reducers
mean = ee.Reducer.mean().unweighted()
sd = ee.Reducer.stdDev().unweighted()
percentiles = ee.Reducer.percentile([10, 25, 50, 75, 90]).unweighted()
allMetrics = mean.combine(sd, sharedInputs=True).combine(percentiles, sharedInputs=True)
# Apply reducers
stm = lALL_masked.reduce(allMetrics)

We can check the outcome by having a quick look at the band names. I do that here by getting the band names for all metrics calculated for the blue band:

In [9]:
bn = stm.bandNames().getInfo()
bn[0:7]

['SR_B2_mean',
 'SR_B2_stdDev',
 'SR_B2_p10',
 'SR_B2_p25',
 'SR_B2_p50',
 'SR_B2_p75',
 'SR_B2_p90']

## Prepare Land Cover variables
That seemed to have worked well. In essence, we have now our independent variables prepared. As dependent variable - again: thematically not the most suitable case - we extract the label of the [ESA World Cover](https://developers.google.com/earth-engine/datasets/catalog/ESA_WorldCover_v200), and add it as an additional band to the SMT image:

In [10]:
# Is an image collection from which we take the first image
esaWC21 = ee.ImageCollection("ESA/WorldCover/v200").select(['Map']).toBands()
# Add to the median composite
allRas = esaWC21.addBands(stm)

## Extract values at the point locations
Now that we have everything ready, we can extract the data for our point locations and store them on our computers. We use the function`.sampleRegions()` to do that. This function works well over smaller areas; for larger areas we need some workaround (see next chapter).

In [11]:
vals = allRas.sampleRegions(collection=fc, properties=['UniqueID'], scale=30, tileScale=4, geometries=False).getInfo()
#vals

the code box below then allows you to convert the `json` dictionary into a `pandas` data frame. It is probably not the smartest option/solution, but it does the job. Feel free to write us with a better option:

In [12]:
flag = 0
featureValues = vals['features']
for f in featureValues:         
 # Chekc here always the right order of the indices
    prop = f['properties']
    if flag == 0:
        out_pd = pd.DataFrame(prop, index=[0])
        flag = 1
    else:
        out_pd = pd.concat([out_pd, pd.DataFrame(prop, index=[0])])
out_pd.head(10)

2021_Map  SR_B2_mean  SR_B2_p10  SR_B2_p25  SR_B2_p50  SR_B2_p75  \
0        10    0.028306   0.018597   0.024840   0.028635   0.036197   
0        50    0.036657   0.005947   0.029350   0.040515   0.049012   
0        10    0.034006   0.021100   0.032485   0.038672   0.043595   
0        10    0.026150   0.015408   0.019532   0.026119   0.031921   
0        10    0.029545   0.004077   0.024070   0.031963   0.039470   
0        10    0.033462   0.023300   0.035098   0.041560   0.048710   
0        10    0.038473   0.026408   0.029955   0.041546   0.045932   
0        10    0.039117   0.030752   0.036720   0.040818   0.046042   
0        80    0.011843  -0.002275   0.010925   0.014651   0.021595   
0        10    0.013181   0.001465   0.011200   0.016453   0.018542   

   SR_B2_p90  SR_B2_stdDev  SR_B3_mean  SR_B3_p10  ...  SR_B6_p90  \
0   0.040763      0.025688    0.047771   0.038425  ...   0.167455   
0   0.053825      0.016171    0.057013   0.016535  ...   0.196385   
0   0.047665      0.026872    0.057391   0.038892  ...   0.196990   
0   0.037751      0.008153    0.043462   0.030203  ...   0.156001   
0   0.043760      0.015874    0.048170   0.017030  ...   0.177163   
0   0.052835      0.033882    0.056933   0.042550  ...   0.199053   
0   0.051708      0.010142    0.055444   0.038123  ...   0.169820   
0   0.049122      0.011361    0.059865   0.048380  ...   0.161185   
0   0.025775      0.017440    0.027680   0.012822  ...   0.037875   
0   0.027535      0.013549    0.034636   0.019065  ...   0.133217   

   SR_B6_stdDev  SR_B7_mean  SR_B7_p10  SR_B7_p25  SR_B7_p50  SR_B7_p75  \
0      0.036227    0.083280   0.053963   0.068867   0.091376   0.100589   
0      0.055205    0.091604   0.015600   0.071095   0.112372   0.122410   
0      0.038173    0.107042   0.072690   0.095515   0.115480   0.127085   
0      0.025951    0.076330   0.053041   0.065664   0.078011   0.089314   
0      0.044934    0.091166   0.064248   0.083085   0.099062   0.110447   
0      0.040876    0.114159   0.083112   0.102665   0.123455   0.134097   
0      0.030425    0.087320   0.062130   0.070242   0.093879   0.102555   
0      0.033179    0.095838   0.074918   0.085175   0.101730   0.110007   
0      0.012331    0.016576   0.006662   0.012190   0.016480   0.018350   
0      0.033203    0.053111   0.032320   0.040378   0.052175   0.059435   

   SR_B7_p90  SR_B7_stdDev  UniqueID  
0   0.105140      0.023167         0  
0   0.128213      0.038036         1  
0   0.131815      0.025410         2  
0   0.094718      0.015321         3  
0   0.119660      0.030530         4  
0   0.140835      0.029419         5  
0   0.107532      0.020293         6  
0   0.115783      0.023472         7  
0   0.027177      0.009429         8  
0   0.065622      0.021263         9  

[10 rows x 44 columns]

## Parameterization in `scikit-learn` and conversion into *GEE*-classifier
The data are ready. We can now move on with the parameterization and the prediction. We will use some pretty cool tools from the `geemap`, including the upload of trained trees beack into *GEE*. We use a random forest classifier to parameterize a model, similar to what we did in the [machine learning session](ch_imgclassification) session.

In [13]:
from sklearn.model_selection import GridSearchCV
from sklearn.ensemble import RandomForestClassifier

In [14]:
# Create the two arrays
y = out_pd['2021_Map']
X = out_pd.drop(['2021_Map', 'UniqueID'], axis=1)
# Create a classifier instance
RF = RandomForestClassifier(random_state=1)
param_grid = {'n_estimators': [10, 25, 50, 75, 100],# 'numberOfTrees
              'max_features': [5, 10, 'sqrt'],# 'variablesPerSplit'
              'min_samples_split': [5, 10, 15], # minLeafPopulation
              'max_depth': [5, 10, 20]} # maxNodes
RF_cv = GridSearchCV(RF, param_grid=param_grid, cv=3, refit=True, n_jobs=4).fit(X, y)
best_mod = RF_cv.best_estimator_

D:\miniforge3\envs\py310\lib\site-packages\sklearn\model_selection\_split.py:725: UserWarning: The least populated class in y has only 2 members, which is less than n_splits=3.
  warnings.warn(


Now, we apply a pretty cool part, implemented in the `geemap` package. What the two functions below are doing is that they (1) convert the random forest model into strings (i.e., the trees), (2) convert it into a feature collection, before (3) converting it into a `ee.Classifer`. For very large models with very long variable names the maximum size of 10MB per model might not be sufficient, but for the problem here it is fine.

```{note}We have found a way to circumvent this problem, and some of it is related to the points we cover in the large-area-section!
```

In [15]:
from geemap import ml
feature_names = X.columns.tolist() # get the names of the variables
best_mod_str = ml.rf_to_strings(best_mod, feature_names)
ee_classifier = ml.strings_to_classifier(best_mod_str)

In [16]:
ee_classifier

## Prediction in GEE and export
Now we have (1) the STM sitting in form of a container in *GEE* and (2) a model which we have trained. All what is needed is to bring these two together through a prediction. This is very easily done through one line of code. Remember, that until you hit `getInfo()` or export the dataset to your drive or into an asset, *GEE* does not a tiny thing of work. Some examples for exporting data were already provided in the [*GEE* raster chapter](ch_imagewf), so we only repeat the code here without muhc explanation.

In [17]:
classification = stm.classify(ee_classifier)

In [ ]:
task = ee.batch.Export.image.toDrive(
    image=classification,
    description='Berlin_Class_Export',
    folder='your_folder',
    fileNamePrefix= 'Berlin_Class_Export',
    region=geomEE,
    scale=30)
task.start()

In [21]:
palette = {'min': 10,'max': 100,
           'palette': ['006400','ffbb22','ffff4c','f096ff','fa0000','b4b4b4','f0f0f0','0064c8','0096a0','00cf75','fae6a0']}
ctr = geomEE.centroid().getInfo()['coordinates']
Map = geemap.Map(center=(ctr[1], ctr[0]), zoom=11)

Map.addLayer(stm, {"bands": ['SR_B7_mean', 'SR_B5_mean', 'SR_B3_mean'], "min": 0.05, "max": 0.55, "gamma": 1.5}, 'image')
Map.addLayer(classification, palette, 'classification')

Map

And that is it. We essentially have used *GEE* as a pure processing and data engine. The advantages of this approach are manyfold:
1. We can have now basically a classification as a *pre-processing* step before doing some more advanced techniques offline which we cannot in *GEE*, such as image segmentation. Think about, for example, a probability image [of a class] which you want to segment using a random walker segmentation. In *GEE* alone you cannot do this, but you also don't want to (a) download all the images, (b) run the pre-processing, and (c) calculate the probabilities before running the segmentation.
2. You can also think about everything else until the model prediction - so, harvesting *GEE* for its data to run all sorts of tests (e.g., different STMs, different images included in a growing season, etc.
3. Sometimes you want to keep you workflow, and maybe even dynamically adjust your training sample, e.g., by using different buffer sizes. You can do all the vector-based manipulation offline and only use *GEE* for the bits of data extraction and processing.

## Further reading
1. [Local Random Forest Training](https://geemap.org/notebooks/46_local_rf_training/)
2. [Classification notebook in EEwPython](https://github.com/csaybar/EEwPython/blob/master/9_SpecializedAlgorithms.ipynb)